In [1]:
import optuna
from lightgbm import LGBMRegressor
from xgboost import XGBRegressor
from catboost import CatBoostRegressor
from sklearn.ensemble import VotingRegressor
from sklearn.model_selection import cross_val_score
from sklearn.metrics import mean_squared_error, r2_score, mean_absolute_error
from sklearn.preprocessing import StandardScaler
from sklearn.model_selection import train_test_split
from sklearn.pipeline import Pipeline
import numpy as np 
import pandas as pd

/home/carolima/.local/lib/python3.10/site-packages/tqdm/auto.py:21: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm


In [2]:
# Load the dataset after the exploratory data analysis
challenge_set_updated = pd.read_csv("./data/challenge_set_updated_v14.csv")
submission_set = pd.read_csv("./data/submission_set.csv")
submission_set_updated = pd.read_csv("./data/submission_set_updated_v14.csv")



In [3]:
# If necessary change this part to test the model before the training process
df = challenge_set_updated.iloc[:,:]
# df = challenge_set_updated.sample(frac=0.001)

# Separating features and target variable
X = df.drop('tow', axis=1)
y = df['tow']



In [4]:
# Define the objective function
def objective(trial):
    global global_model_pipeline
    # Sample hyperparameters for LightGBM
    lgb_params = {
        'n_estimators': trial.suggest_int('lgb_n_estimators', 50, 1000),
        'learning_rate': trial.suggest_float('lgb_learning_rate', 0.001, 0.5),
        'max_depth': trial.suggest_int('lgb_max_depth', 3, 15),
        'num_leaves': trial.suggest_int('lgb_num_leaves', 31, 1024),
        'reg_alpha': trial.suggest_float('lgb_reg_alpha', 0, 10),
        'reg_lambda': trial.suggest_float('lgb_reg_lambda', 0, 10),
    }

    # Sample hyperparameters for XGBoost
    xgb_params = {
        'n_estimators': trial.suggest_int('xgb_n_estimators', 50, 1000),
        'learning_rate': trial.suggest_float('xgb_learning_rate', 0.001, 0.5),
        'max_depth': trial.suggest_int('xgb_max_depth', 3, 15),
        'subsample': trial.suggest_float('xgb_subsample', 0.5, 1.0),
        'colsample_bytree': trial.suggest_float('xgb_colsample_bytree', 0.5, 1.0),
        'reg_alpha': trial.suggest_float('xgb_reg_alpha', 0, 10),
        'reg_lambda': trial.suggest_float('xgb_reg_lambda', 0, 10),
    }

    # Sample hyperparameters for CatBoost
    cat_params = {
        'n_estimators': trial.suggest_int('cat_n_estimators', 50, 1000),
        'learning_rate': trial.suggest_float('cat_learning_rate', 0.001, 0.5),
        'depth': trial.suggest_int('cat_depth', 3, 15),
        'l2_leaf_reg': trial.suggest_float('cat_l2_leaf_reg', 1, 10),
    }

    # Initialize the models with sampled hyperparameters
    lgb_model = LGBMRegressor(**lgb_params)
    xgb_model = XGBRegressor(**xgb_params, objective='reg:squarederror')
    cat_model = CatBoostRegressor(**cat_params, verbose=0)

    # Ensemble the models using VotingRegressor
    ensemble_model = VotingRegressor(
        estimators=[
            ('lgb', lgb_model),
            ('xgb', xgb_model),
            ('cat', cat_model)
        ]
    )

    # Create a pipeline with data scaling and the ensemble model
    model_pipeline = Pipeline([
        ('scaler', StandardScaler()),
        ('ensemble', ensemble_model)
    ])

    # Split the dataset (use your own dataset instead of X, y)
    X_train, X_valid, y_train, y_valid = train_test_split(X, y, test_size=0.2, random_state=42)

    # Train the ensemble model
    model_pipeline.fit(X_train, y_train)

    # Make predictions
    y_pred = model_pipeline.predict(X_valid)

    # Calculate metrics
    rmse = mean_squared_error(y_valid, y_pred, squared=False)
    r2 = r2_score(y_valid, y_pred)
    mae = mean_absolute_error(y_valid, y_pred)

    global_model_pipeline = model_pipeline

    return rmse  # Use Optuna to optimize RMSE (can add r2 or mae as well)

In [5]:
# Run Optuna study
study = optuna.create_study(direction='minimize')
study.optimize(objective, n_trials=100)

# Print the best parameters
print("Best parameters:", study.best_params)
print("Best RMSE:", study.best_value)

[I 2024-10-11 18:39:48,594] A new study created in memory with name: no-name-33ae3ecd-1b26-4657-9f56-851159e5e603


[LightGBM] [Info] Auto-choosing col-wise multi-threading, the overhead of testing was 0.071723 seconds.
You can set `force_col_wise=true` to remove the overhead.
[LightGBM] [Info] Total Bins 18260
[LightGBM] [Info] Number of data points in the train set: 295210, number of used features: 420
[LightGBM] [Info] Start training from score 79542.054059
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf


/home/carolima/.local/lib/python3.10/site-packages/sklearn/metrics/_regression.py:492: FutureWarning: 'squared' is deprecated in version 1.4 and will be removed in 1.6. To calculate the root mean squared error, use the function'root_mean_squared_error'.
  warnings.warn(
[I 2024-10-11 18:40:27,409] Trial 0 finished with value: 2698.8120404733704 and parameters: {'lgb_n_estimators': 181, 'lgb_learning_rate': 0.1262072480200381, 'lgb_max_depth': 10, 'lgb_num_leaves': 117, 'lgb_reg_alpha': 4.708343198100261, 'lgb_reg_lambda': 9.740821055130082, 'xgb_n_estimators': 271, 'xgb_learning_rate': 0.20262953283505214, 'xgb_max_depth': 7, 'xgb_subsample': 0.5992418268261301, 'xgb_colsample_bytree': 0.5715862116559896, 'xgb_reg_alpha': 3.185460569322079, 'xgb_reg_lambda': 4.670945011723383, 'cat_n_estimators': 209, 'cat_learning_rate': 0.3050794417258561, 'cat_depth': 7, 'cat_l2_leaf_reg': 6.646663465443108}. Best is trial 0 with value: 2698.8120404733704.


[LightGBM] [Info] Auto-choosing col-wise multi-threading, the overhead of testing was 0.059882 seconds.
You can set `force_col_wise=true` to remove the overhead.
[LightGBM] [Info] Total Bins 18260
[LightGBM] [Info] Number of data points in the train set: 295210, number of used features: 420
[LightGBM] [Info] Start training from score 79542.054059
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positiv

/home/carolima/.local/lib/python3.10/site-packages/sklearn/metrics/_regression.py:492: FutureWarning: 'squared' is deprecated in version 1.4 and will be removed in 1.6. To calculate the root mean squared error, use the function'root_mean_squared_error'.
  warnings.warn(
[I 2024-10-11 18:40:55,296] Trial 1 finished with value: 2796.289934421357 and parameters: {'lgb_n_estimators': 956, 'lgb_learning_rate': 0.36820465237735195, 'lgb_max_depth': 3, 'lgb_num_leaves': 914, 'lgb_reg_alpha': 5.016259090504411, 'lgb_reg_lambda': 5.1789815782509905, 'xgb_n_estimators': 242, 'xgb_learning_rate': 0.08570633870045233, 'xgb_max_depth': 5, 'xgb_subsample': 0.9130556508730943, 'xgb_colsample_bytree': 0.8455111832863489, 'xgb_reg_alpha': 3.8251396209847135, 'xgb_reg_lambda': 3.699129535854645, 'cat_n_estimators': 431, 'cat_learning_rate': 0.4794417886212759, 'cat_depth': 5, 'cat_l2_leaf_reg': 9.153644420752473}. Best is trial 0 with value: 2698.8120404733704.


...

[LightGBM] [Info] Auto-choosing col-wise multi-threading, the overhead of testing was 0.068725 seconds.
You can set `force_col_wise=true` to remove the overhead.
[LightGBM] [Info] Total Bins 18260
[LightGBM] [Info] Number of data points in the train set: 295210, number of used features: 420
[LightGBM] [Info] Start training from score 79542.054059
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positiv

/home/carolima/.local/lib/python3.10/site-packages/sklearn/metrics/_regression.py:492: FutureWarning: 'squared' is deprecated in version 1.4 and will be removed in 1.6. To calculate the root mean squared error, use the function'root_mean_squared_error'.
  warnings.warn(
[I 2024-10-12 01:37:18,106] Trial 98 finished with value: 2658.2121475804593 and parameters: {'lgb_n_estimators': 927, 'lgb_learning_rate': 0.39507063096001616, 'lgb_max_depth': 9, 'lgb_num_leaves': 804, 'lgb_reg_alpha': 2.3034066816109835, 'lgb_reg_lambda': 0.23734596189473028, 'xgb_n_estimators': 146, 'xgb_learning_rate': 0.12635435585557947, 'xgb_max_depth': 4, 'xgb_subsample': 0.7709793310124261, 'xgb_colsample_bytree': 0.8000365100641987, 'xgb_reg_alpha': 2.701393327025559, 'xgb_reg_lambda': 1.6355910473977753, 'cat_n_estimators': 852, 'cat_learning_rate': 0.42050549271175963, 'cat_depth': 10, 'cat_l2_leaf_reg': 7.867550220927344}. Best is trial 12 with value: 2465.8630780700814.


[LightGBM] [Info] Auto-choosing col-wise multi-threading, the overhead of testing was 0.058512 seconds.
You can set `force_col_wise=true` to remove the overhead.
[LightGBM] [Info] Total Bins 18260
[LightGBM] [Info] Number of data points in the train set: 295210, number of used features: 420
[LightGBM] [Info] Start training from score 79542.054059
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positiv

/home/carolima/.local/lib/python3.10/site-packages/sklearn/metrics/_regression.py:492: FutureWarning: 'squared' is deprecated in version 1.4 and will be removed in 1.6. To calculate the root mean squared error, use the function'root_mean_squared_error'.
  warnings.warn(
[I 2024-10-12 01:39:22,652] Trial 99 finished with value: 2552.8228016771163 and parameters: {'lgb_n_estimators': 807, 'lgb_learning_rate': 0.13154841306437498, 'lgb_max_depth': 4, 'lgb_num_leaves': 756, 'lgb_reg_alpha': 0.9523217873909963, 'lgb_reg_lambda': 5.416068618887344, 'xgb_n_estimators': 196, 'xgb_learning_rate': 0.08284567329947592, 'xgb_max_depth': 11, 'xgb_subsample': 0.8066142138240087, 'xgb_colsample_bytree': 0.7725170877642301, 'xgb_reg_alpha': 1.9968728849133348, 'xgb_reg_lambda': 0.5577939200944089, 'cat_n_estimators': 897, 'cat_learning_rate': 0.33320632268654105, 'cat_depth': 11, 'cat_l2_leaf_reg': 9.773680952676724}. Best is trial 12 with value: 2465.8630780700814.


Best parameters: {'lgb_n_estimators': 327, 'lgb_learning_rate': 0.10468081141850077, 'lgb_max_depth': 12, 'lgb_num_leaves': 413, 'lgb_reg_alpha': 9.497313637328773, 'lgb_reg_lambda': 0.25602838363607994, 'xgb_n_estimators': 697, 'xgb_learning_rate': 0.1517686404182979, 'xgb_max_depth': 11, 'xgb_subsample': 0.8495330246990868, 'xgb_colsample_bytree': 0.8100349312632752, 'xgb_reg_alpha': 6.644078141788623, 'xgb_reg_lambda': 6.430948138368547, 'cat_n_estimators': 709, 'cat_learning_rate': 0.20930564781071165, 'cat_depth': 11, 'cat_l2_leaf_reg': 1.3003733988635693}
Best RMSE: 2465.8630780700814


In [6]:
# Extract features for prediction
submission_set_features = submission_set_updated.iloc[:, :-1]

model_pipeline = global_model_pipeline

# Predict using the fitted pipeline (which includes scaling and the ensemble model)
submission_set['tow'] = model_pipeline.predict(submission_set_features)

# Output the predictions
print(submission_set)

        flight_id        date                          callsign  adep  \
0       248753821  2022-01-01  3b3de0f3ad0ee192513995c02f7bf7cf  LTFJ   
1       248753822  2022-01-01  e06dd03d4a879ca37d9e18c1bd7cad16  EBBR   
2       248754498  2022-01-01  2d3b1c962c78c4ebeef11bcd51b9e94c  KMIA   
3       248757623  2022-01-01  81564432d3ee97c4bdf4cd8f006753dc  EGCN   
4       248763603  2022-01-01  84be079d7e660db105d91f600b4b3d59  EIDW   
...           ...         ...                               ...   ...   
105954  258066302  2022-12-31  2d3b4446c4d05a25196a9d52cab936fb  LTFJ   
105955  258068609  2022-12-31  253fd692ed441fac523081471c067772  LOWW   
105956  258068876  2022-12-31  c9fca302ca2e28acab0eb0bb1b46f11b  LTFM   
105957  258064675  2022-12-31  00f96ad0e382476649574ba044c764fc  EHAM   
105958  258058370  2022-12-31  5f0c222c7f7ceff3fbe75c854cce74c9  UBBB   

                     name_adep country_code_adep  ades          name_ades  \
0       Istanbul Sabiha Gokcen                

In [7]:
import os
from datetime import datetime

# Define the submissions directory and create it if it doesn't exist
submissions_dir = 'submissions'
os.makedirs(submissions_dir, exist_ok=True)

# Define a timestamp for the file name
timestamp = datetime.now().strftime("%Y%m%d_%H%M%S")

# Save the submission with a timestamp in the filename
submission_file = os.path.join(submissions_dir, f"submission_{timestamp}.csv")

# Assuming submission_set is a DataFrame, save it to CSV
submission_set.to_csv(submission_file, index=False)

print(f"Submission saved to {submission_file}")


Submission saved to submissions/submission_20241012_013923.csv
